# MDD: Web Scraping - La liga 2022-2023
#### Autor: Julen Beristain Oliden

## 1. Objetivo

El objetivo de este trabajo es recopilar estadísticas de la primera división de la liga española de fútbol profesional durante la temporada 2022-2023.

## 2. Preparación

Para llevar a cabo nuestro objetivo, lo primero es encontrar la fuente de información. Para ello, encontré una página en el sitio web ["bcoach"](https://bcoach.app/mejor-web-estadisticas-futbol/) con una recopilación de las mejores webs de estadísticas de fútbol. Tras curiosear por ellas, me decanté por ["Besoccer"](https://es.besoccer.com/). En el apartado "competiciones" - "primera división" tenemos una página donde podemos elegir la temporada que nos interesa. Además de la temporada, podemos ir cambiando la jornada en la misma página, y nos van apareciendo los resultados y los links a los partidos de esa misma jornada.

Una vez tenemos la fuente de información, necesitamos una manera automitazada de obtener las estadísticas de los 380 partidos de la temporada. Para ello, he decidido utilizar la librería ["BeautifulSoup"](https://www.crummy.com/software/BeautifulSoup/bs4/doc/#bs4.Tag.attrs) para hacer web scraping; es decir, obtener información del código fuente HTML de las páginas de los partidos. También hago uso de la librería ["Requests"](https://requests.readthedocs.io/en/latest/) para obtener los HTML de los códigos de los partidos. Con esto parecería suficiente, pero como he dicho antes, la jornada seleccionada se actualiza de manera dinámica mediante JavaScript en la misma página. Por ello, para automatizar también el recorrido a través de las 38 jornadas, he utilizado ["Selenium"](https://www.selenium.dev/), el cual permite crear "bots" que abren el navegador web automáticamente e interactuan con los elementos de las páginas dinámicamente.

Para terminar con las herramientas utilizadas, no basta con guardar en memoria las estadísticas de los partidos. Queremos que esa información perdure en formatos estándar para bases de datos. En nuestro caso, los formatos .csv y .arff que llevamos empleando a lo largo del curso. Por ello, he utilizado la librería estándar [csv](https://docs.python.org/3/library/csv.html#) de Python y la librería [liac-arff](https://pypi.org/project/liac-arff/). Esta última no es estándar, y podríamos haber planteado de otra forma la consecución del archivo en formato .arff, como por ejemplo traducir el .csv a .arff ya sea con Python o ya sea con WEKA mismamente, pero es la librería más reciente para trabajar con archivos .arff y funciona.

Junto con este notebook de Collab también envío el script de Python que desarrollamos aquí, pero al ejecutarlo en local hará falta que las librerías estén instaladas y que el web driver de Chrome (ChromeDrive) esté correctamente configurado (en mi caso lo estaba por defecto, eso no me ha dado mayores problemas) al usar Selenium. Para utilizar estas herramientas en Google Collab, eso sí, hará falta instalar e importar las librerías, obtener el web driver actualizado de Chrome y definir una función que nos dé el objeto "webdriver" de la librería de Selenium con las opciones correctas para este entorno:

In [1]:
!python -m pip install requests
!pip install liac-arff
!pip install selenium

  Preparing metadata (setup.py) ... done
  Created wheel for liac-arff: filename=liac_arff-2.5.0-py3-none-any.whl size=11716 sha256=4f21ad36c83eeeb3a5fe8520541ceedbe2963976ca5e290899b01dec74e00a61
  Stored in directory: /root/.cache/pip/wheels/5d/2a/9c/3895d9617f8f49a0883ba686326d598e78a1c2f54fe3cae86d
Successfully built liac-arff
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.0/10.0 MB 20.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 461.6/461.6 kB 36.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 1.1 MB/s eta 0:00:00


In [2]:
# Actualizar el web-driver de Chrome en el servidor para poder usar Selenium
!apt-get update
!apt-get install chromium chromium-driver

Get:1 https://cloud.r-project.org/bin/linux/ubuntu jammy-cran40/ InRelease [3,626 B]
Hit:2 http://archive.ubuntu.com/ubuntu jammy InRelease
Get:3 http://security.ubuntu.com/ubuntu jammy-security InRelease [110 kB]
Hit:4 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu2204/x86_64  InRelease
Get:5 http://archive.ubuntu.com/ubuntu jammy-updates InRelease [119 kB]
Hit:6 https://ppa.launchpadcontent.net/c2d4u.team/c2d4u4.0+/ubuntu jammy InRelease
Hit:7 https://ppa.launchpadcontent.net/deadsnakes/ppa/ubuntu jammy InRelease
Hit:8 http://archive.ubuntu.com/ubuntu jammy-backports InRelease
Hit:9 https://ppa.launchpadcontent.net/graphics-drivers/ppa/ubuntu jammy InRelease
Hit:10 https://ppa.launchpadcontent.net/ubuntugis/ppa/ubuntu jammy InRelease
Get:11 http://security.ubuntu.com/ubuntu jammy-security/restricted amd64 Packages [1,582 kB]
Get:12 http://archive.ubuntu.com/ubuntu jammy-updates/restricted amd64 Packages [1,611 kB]
Get:13 http://security.ubuntu.com/ubuntu jammy-securi

In [3]:
from bs4 import BeautifulSoup
#import lxml

import requests
from selenium import webdriver
#from selenium.webdriver.support.ui import Select
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC

import arff
import csv

import time

In [4]:
# Para usar el driver en Google Collab no nos sirven las opciones por defecto
def web_driver():
    options = webdriver.ChromeOptions()
    options.add_argument("--verbose")
    options.add_argument('--no-sandbox')
    options.add_argument('--headless')
    options.add_argument('--disable-gpu')
    options.add_argument("--window-size=1920, 1200")
    options.add_argument('--disable-dev-shm-usage')
    driver = webdriver.Chrome(options=options)
    return driver


Cabe mencionar que no es necasario importar la librería "lxml", pero si pretendemos utilizarla como parser al generar el objeto BeatifulSoup hace falta tenerla instalada. El import comentado de la clase "Select" de Selenium y el del módulo estándar "time" se explican en el apartado en el que desarrollamos el código.

Con esto, estamos (casi) listos para desarrolar el script con el que obtendremos las estadísticas del sitio Besoccer.

## 3. Desarrollo

Tenemos todas las herramientas necesarias, pero eso no basta para ponernos manos a la obra con el código. Es necesario analizar la estructura HTML de las páginas que vamos a scrapear y ver cuales son las estadísticas de los partidos que podremos recoger. En función a ello, definiremos la estructura de nuestra base de datos. Por otro lado, el grado de cuanto tendremos que complicarnos al usar BeuatifulSoup dependerá también de cuán bien estructurados estén las páginas de los partidos.

Después de haber mirado partidos de varias jornadas (y de haber verificado con asserts ya una vez ejecutado el script completo) podemos observar que hay ciertos partidos que tienen más estadísticas que otros, y que a partir de cierta jornada la estadística de porcentaje de pases precisos se muestra de otra forma (estos pequeños detalles se comentan en las partes del código donde tienen influencia). Utilizaremos el conjunto de estadísticas del partido que tiene más estadísticas en nuestra base de datos. Para los partidos que no tengan cierta estadística, ese valor va a quedar como nulo (string vacío o "?" en los archivos csv y arff, respectivamente) en la base de datos. Así, esta es la definición:

* Filas:
  * Cada fila de nuestra base de datos se corresponde a un partido desde el punto de vista de uno de los dos equipos.
  * Por ende, el número de instancias es igual a 380 · 2 = 760.

* Columnas:
  * Datos generales: codigo del partido (lo genero yo, empezando desde 1 hasta 380), fecha, hora, goles, equipo, resultado (victoria, empate o derrota).

    * Como nota adicional para fecha y hora, cabe mencionar que obtengo valores distintos al scrapear en Google Collab o en local, incluso usando el mismo script (con la única diferencia de la necesidad de usar la función web_driver definida en el apartado anterior). Los valores correctos los obtengo en local, que son las bases de datos que entrego.

  * Datos del juego:
    * Generales: posesión, fueras de juego, saques de esquina, duelos ganados, duelos perdidos.
    * Ataque: tiros totales, tiros fuera, tiros a puerta, tiros dentro del área, tiros desde fuera del área, disparos bloqueados, ataques, ataques peligrosos.
    * Defensa: paradas, entradas.
    * Distribución: pases, pases precisos, porcentaje de pases precisos.
    * Disciplina: faltas, tarjetas amarillas, tarjetas rojas.

* La variable clase es "resultado", y todas las demás son predictoras.

La siguiente variable del script me ha servido para comprobar con un assert que entre las estadísticas de juego que consigo al scrapear todos los partidos no hay ninguna del que me haya olvidado:




In [5]:
# Todos las estadísticas encontradas en las estadisticas de las páginas de los pártidos del sitio Besoccer
possible_stat_names = ["Posesión", "Fueras de juego", "Saques de esquina", "Duelos ganados", "Duelos perdidos",                         #GENERALES
                       "Tiros totales", "Tiros fuera", "Tiros a puerta",                                                                #ATAQUE
                       "Tiros dentro del área", "Tiros desde fuera del área", "Disparos bloqueados", "Ataques", "Ataques Peligrosos",   #ATAQUE
                       "Paradas", "Entradas",                                                                                           #DEFENSA
                       "Pases", "Pases precisos", "Porcentaje de pases precisos", "Pases completados",                                  #DISTRIBUCIÓN
                       "Faltas", "Tarjetas amarillas", "Tarjetas rojas"]                                                                #DISCIPLINA

Ahora toca ir haciendo el código para scrapear las páginas de cada partido. Primero, las estadísticas generales, aprovechando los nombres de los tags ("span" y "div") y las clases CSS ("r1", "r2" y "header-match-date") correspondientes a los datos:

In [17]:
def obtain_general_stats(soup, match_id):
    #print("\n\tDatos generales del partido:")

    # Aparecen otros partidos cuyos resultados se guardan en "span" con las clases "r1" y "r2"
    # El número de los partidos "extra" cambia en cada página
    # La información del partido de la página se encuentra después
    # Por ello, eligiendo el último "span" nos aseguramos de elegir el resultado deseado
    goles_local = int(soup.find_all("span", class_="r1")[-1].string)
    goles_visitante = int(soup.find_all("span", class_="r2")[-1].string)
    #print(f"Goles local: {goles_local}")
    #print(f"Goles visitante: {goles_visitante}")

    assert(1 <= match_id <= 380) #No lo intenten en otros (muchos) lenguajes
    #print(f"Código de partido: {match_id}")

    fecha_y_hora = soup.find("div", class_="header-match-date").string
    #print(f"Fecha y hora: {fecha_y_hora}")

    equipo_local, equipo_visitante = (p_tag.a.string for p_tag in soup.find_all("p", class_="name")[:2])
    #print(f"Equipo local: {equipo_local}")
    #print(f"Equipo visitante: {equipo_visitante}")

    if goles_local > goles_visitante:
        resultado_local, resultado_visitante = "Victoria", "Derrota"
    elif goles_local < goles_visitante:
        resultado_local, resultado_visitante = "Derrota", "Victoria"
    else:
        resultado_local, resultado_visitante = "Empate", "Empate"
    #print(f"Resultado local: {resultado_local}")
    #print(f"Resultado visitante: {resultado_visitante}")

    return goles_local, goles_visitante, fecha_y_hora, equipo_local, equipo_visitante, \
           resultado_local, resultado_visitante

Segundo, todos los datos del juego exceptuando "tiros fuera" y "tiros a puerta", que debido a su disposición ligeramente distinta en la página, el HTML que los envuelve es diferente. Todos los demás se pueden obtener encontrando "div"s con atributo class "td-num left/right" (como veremos más adelante en la llamada e esta función). En cuanto a la estadística "posesión", como el nombre de la estadística aparece en un tag "p", no está en el bucle junto a todas las demás. Y con respecto a "porcentaje de pases precisos", en vez de tener su fila como las demás estadísticas, a partir de cierta jornada aparece al lado de la estadística de pases completados (comparar cualquier partido de la primera jornada con cualquiera de la última para verlo), por lo que dentro del "div" quedan más strings. Por ello, usamos un condicional para distinguir los dos casos:

In [7]:
def obtain_non_exceptional_stats(soup, div_class_attribute):
    info_divs = soup.find_all("div", class_ = div_class_attribute)

    info_dict = dict()

    #Posesión es diferente: está dentro de un tag <p>, su parte en el html es distinto
    info_dict["Posesión"] = int(info_divs[0].span.string[:-1])
    #print(f"Posesión: {info_dict['Posesión']}")

    for i in range(1, len(info_divs)):
        div = info_divs[i]
        stat_data = int(div.span.string)
        stat_names = list(div.parent.stripped_strings)
        #En ciertas jornadas el "Porcentaje de pases precisos" aparece en la misma línea de "Pases completados"
        assert(len(stat_names) == 3 or len(stat_names) == 5)
        if len(stat_names) == 3:
            stat_name = stat_names[1]
        elif len(stat_names) == 5:
            info_dict["Porcentaje de pases precisos"] = int(stat_names[1][1:3])
            #print(f"Porcentaje de pases precisos: {info_dict['Porcentaje de pases precisos']}")
            stat_name = "Pases precisos"
        assert(stat_name in possible_stat_names)
        info_dict[stat_name] = stat_data
        #print(f"{stat_name}: {stat_data}")

    return info_dict

Y también por supuesto a las ya mencionadas excepciones:

In [8]:
def obtain_exceptional_stats(soup):
    #print("\n\tTiros fuera:")
    tiros_fuera_local = int(soup.find("span", class_="num left").string)
    tiros_fuera_visitante = int(soup.find("span", class_="num right").string)
    #print("Tiros fuera local:", tiros_fuera_local)
    #print("Tiros fuera visitante:", tiros_fuera_visitante)

    #print("\n\tTiros a puerta:")
    tiros_a_puerta_local = int(soup.find("span", class_="pl15").string)
    tiros_a_puerta_visitante = int(soup.find("span", class_="pr15").string)
    #print("Tiros a puerta local:", tiros_a_puerta_local)
    #print("Tiros a puerta visitante:", tiros_a_puerta_visitante)

    return tiros_fuera_local, tiros_fuera_visitante, \
           tiros_a_puerta_local, tiros_a_puerta_visitante

Para terminar con las funciones auxiliares, defino una función para separar el string de la fecha y la hora en dos distintos en el formato que me interesa...

In [9]:
#Formato fecha_y_hora: 27 MAY 2023 19:00
def split_fecha_y_hora(fecha_y_hora):
    meses_dict = {'AGO': '8',
                  'SEP': '9',
                  'OCT': '10',
                  'NOV': '11',
                  'DIC': '12',
                  'ENE': '01',
                  'FEB': '02',
                  'MAR': '03',
                  'ABR': '04',
                  'MAY': '05',
                  'JUN': '06'}

    elementos = fecha_y_hora.strip().split()
    fecha = f'{elementos[0]}-{meses_dict[elementos[1]]}-{elementos[2]}'
    hora = elementos[-1]
    return fecha, hora

... y la utilizo al inicio de la última función auxiliar, el cual introduce en la lista "data" el diccionario (pares clave-valor, nombre de la estadística - valor de la estadística) correspondiente al partido:

In [10]:
# Importante el uso del método get de los diccionarios auxiliares previamente generados para
# poner el string vacío como valor para las estadísticas no disponibles en un partido
def introduce_row(data, fecha_y_hora, goles, equipo, resultado, dict_, tiros_fuera, tiros_a_puerta):
    fecha, hora = split_fecha_y_hora(fecha_y_hora)

    stats = {
            "codigo_partido" : match_id,
            "fecha" : fecha,
            "hora" : hora,
            "goles" : goles,
            "equipo" : equipo,
            "resultado" : resultado,
            "posesion" : dict_.get("Posesión", ""),
            "fueras_de_juego" : dict_.get("Fueras de juego", ""),
            "saques_de_esquina" : dict_.get("Saques de esquina", ""),
            "duelos_ganados" : dict_.get("Duelos ganados", ""),
            "duelos_perdidos" : dict_.get("Duelos perdidos", ""),
            "tiros_totales" : dict_.get("Tiros totales", ""),
            "tiros_fuera" : tiros_fuera,
            "tiros_a_puerta" : tiros_a_puerta,
            "tiros_dentro_del_area" : dict_.get("Tiros dentro del área", ""),
            "tiros_desde_fuera_del_area" : dict_.get("Tiros desde fuera del área", ""),
            "disparos_bloqueados" : dict_.get("Disparos bloqueados", ""),
            "ataques" : dict_.get("Ataques", ""),
            "ataques_peligrosos" : dict_.get("Ataques Peligrosos", ""),
            "paradas" : dict_.get("Paradas", ""),
            "entradas" : dict_.get("Entradas", ""),
            "pases" : dict_.get("Pases", ""),
            "pases_completados" : dict_.get("Pases precisos", ""),
            "porcentaje_pases_completados" : dict_.get("Porcentaje de pases precisos", ""),
            "faltas" : dict_.get("Faltas", ""),
            "tarjetas_amarillas" : dict_.get("Tarjetas amarillas", ""),
            "tarjetas_rojas" : dict_.get("Tarjetas rojas", "")
            }

    data.append(stats)

Así, la función para obtener las estadísticas de un partido queda así: recibo el link de la página del partido, el id generado por mí del partido (en la parte del código que falta por ver) y la lista que contiene los diccionarios de cada partido. Utilizo la librería Requests para obtener el HTML de la página y genero el objeto BeautifulSoup que servirá para analizar el HTML. De esta forma, uso dicho objeto en las funciones anteriores para obtener los datos e insertarlos en "data" (dos diccionarios, uno desde el punto de vista del equipo local y otro del visitante):

In [11]:
def obtain_match_statistics(link, match_id, data):
    page_html = requests.get(link).text
    soup = BeautifulSoup(page_html, "lxml")

    #OBTENER LOS DATOS

    goles_local, goles_visitante, fecha_y_hora, equipo_local, equipo_visitante, \
        resultado_local, resultado_visitante = obtain_general_stats(soup, match_id)

    #print("\n\tInformación del equipo local (todo salvo tiros fuera y tiros a puerta):")
    local_dict = obtain_non_exceptional_stats(soup, "td-num left")

    #print("\n\tInformación del equipo visitante (todo salvo tiros fuera y tiros a puerta):")
    visitante_dict = obtain_non_exceptional_stats(soup, "td-num right")

    tiros_fuera_local, tiros_fuera_visitante, \
        tiros_a_puerta_local, tiros_a_puerta_visitante = obtain_exceptional_stats(soup)

    #INTRODUCIR LOS DATOS

    introduce_row(
        data, fecha_y_hora, goles_local, equipo_local, resultado_local,
        local_dict, tiros_fuera_local, tiros_a_puerta_local)
    introduce_row(
        data, fecha_y_hora, goles_visitante, equipo_visitante, resultado_visitante,
        visitante_dict, tiros_fuera_visitante, tiros_a_puerta_visitante)

Una vez tenemos el código para obtener todos los datos de un partido, necesitamos poder iterar automáticamente sobre todas las jornadas, consiguiendo los links de todos los partidos y llamando a la función anterior. Aquí es donde utilizamos la librería Selenium. Es posiblemente la parte que más quebraderos de cabeza me ha dado, porque al desarrollar el script empecé a hacerlo en un notebook de Collab, lo cual no me permitía ver como funcionaba el bot al abrir el navegador. Por ello, pase a desarrollarlo en local, y me di cuenta de la necesidad de aceptar las cookies antes de poder interactuar con los demás elementos de la página. Otro punto importante es que hay que localizar el elemento "select" que sirve para elegir la jornada cada vez que el código HTML se actualiza dinámicamente, es decir, cada vez que cambiamos de jornada (para ello se pone su línea correspondiente al inicio del for). El punto más complicado ha sido que la manera estándar de la librería Selenium para trabajar con elementos "select" no me funcionaba (crear el objeto Select y emplear uno de sus métodos para seleccionar una opción) por lo que he tenido que usar el recurso que nos ofrece el objeto Driver de Selenium para ejecutar pequeños scripts de JavaScript para interactuar con el mencionado "select" dinámicamente. El último detalle importante es que una vez ejecutado dicho script, es imprescindible esperar un poco para que la página se actualice, y por ello uso la librería estándar time y su función sleep:

In [ ]:
#################################################################################
### Iterar sobre todas las jornadas consiguiendo los links de todos los partidos

url_temporada = "https://es.besoccer.com/competicion/resultados/primera/2023"
driver = web_driver() #en local simplemente: webdriver.Chrome()
driver.get(url_temporada)

# Aceptar las cookies
driver.find_element(By.XPATH, "//button[.//span[text()='ACEPTO']]").click()

match_id = 0
data = [] #lista de diccionarios de cada fila en nuestro dataset

for jornada in range(38):
    select_element = WebDriverWait(driver, 10).until(
    EC.presence_of_element_located((By.CSS_SELECTOR, 'select.select-control.mb0'))
    )

    driver.execute_script(f"arguments[0].selectedIndex = {jornada};", select_element)
    driver.execute_script("arguments[0].dispatchEvent(new Event('change'))", select_element)

    #Forma estándar de trabajar en Selenium (no me funciona):
    #select = Select(select_element)
    #select.select_by_index(jornada)

    # Esperar a que la página se cargue, sino, los nuevos links no habrán aparecido
    time.sleep(2)

    updated_html = driver.page_source
    soup = BeautifulSoup(updated_html, 'lxml')

    print(f"############ JORNADA {jornada+1}: ############\n")
    links_partidos = [match_div.a["href"] for match_div in soup.find_all("div", class_="match-link")]
    assert(len(links_partidos) == 10)
    for l in links_partidos:
        #print(l, type(l))
        match_id += 1
        print(f"### PARTIDO {match_id}: ###")
        obtain_match_statistics(l, match_id, data)
        #print()
    #print()

# Cerrar el navegador
driver.quit()

En este punto, ya tenemos en la lista "data" los diccionarios de cada fila de nuestra base de datos. Lo único que falta es guardarlo en los archivos .csv y .arff resultantes. El código para ello queda un poco "verbose" debido a la cantidad de columnas y la necesidad de escribir sus strings, pero una vez escrito, el código es muy sencillo:

In [16]:
####################################################
# Guardamos en un csv los datos almacenados en data
with open("liga_2022_23.csv", 'w', encoding='utf-8', newline='') as csvfile:
    fieldnames = ['codigo_partido',
                  'fecha',
                  'hora',
                  'goles',
                  'posesion',
                  'fueras_de_juego',
                  'saques_de_esquina',
                  'duelos_ganados',
                  'duelos_perdidos',
                  'tiros_totales',
                  'tiros_fuera',
                  'tiros_a_puerta',
                  'tiros_dentro_del_area',
                  'tiros_desde_fuera_del_area',
                  'disparos_bloqueados',
                  'ataques',
                  'ataques_peligrosos',
                  'paradas',
                  'entradas',
                  'pases',
                  'pases_completados',
                  'porcentaje_pases_completados',
                  'faltas',
                  'tarjetas_amarillas',
                  'tarjetas_rojas',
                  'equipo',
                  'resultado']
    writer = csv.DictWriter(csvfile, fieldnames=fieldnames)

    # Escribir la cabecera
    writer.writeheader()

    # Escribir cada fila guardada en "data"
    for entry in data:
        writer.writerow(entry)

description = \
"""
Creador: Julen Beristain Oliden, Informatika Fakultatea, Donostia, UPV-EHU, en base a
         un trabajo de Web Scraping de la asignatura Minería de Datos.

La siguiente base de datos recoge algunos datos estadísticos de los partidos de fútbol
disputados en la primera división de la liga española durante la temporada 2022-2023.

Cada partido es transformado en dos filas en este fichero, una por cada equipo: cada una
recoge los datos del equipo en ese partido. Las dos filas aparecen de forma contigua en el fichero.

De esta manera, para cada par de instancias provenientes de un partido, una de las dos es etiquetada
como "Victoria", la otra como "Derrota", o las dos como "Empate".
"""

####################################################
# Guardamos en un arff los datos almacenados en data
arff_dict = {
    'description': description,
    'relation': 'liga_2022_23',
    'attributes': [
        ('codigo_partido', 'NUMERIC'),
        ('fecha', 'STRING'),
        ('hora', 'STRING'),
        ('goles', 'NUMERIC'),
        ('posesion', 'NUMERIC'),
        ('fueras_de_juego', 'NUMERIC'),
        ('saques_de_esquina', 'NUMERIC'),
        ('duelos_ganados', 'NUMERIC'),
        ('duelos_perdidos', 'NUMERIC'),
        ('tiros_totales', 'NUMERIC'),
        ('tiros_fuera', 'NUMERIC'),
        ('tiros_a_puerta', 'NUMERIC'),
        ('tiros_dentro_del_area', 'NUMERIC'),
        ('tiros_desde_fuera_del_area', 'NUMERIC'),
        ('disparos_bloqueados', 'NUMERIC'),
        ('ataques', 'NUMERIC'),
        ('ataques_peligrosos', 'NUMERIC'),
        ('paradas', 'NUMERIC'),
        ('entradas', 'NUMERIC'),
        ('pases', 'NUMERIC'),
        ('pases_completados', 'NUMERIC'),
        ('porcentaje_pases_completados', 'NUMERIC'),
        ('faltas', 'NUMERIC'),
        ('tarjetas_amarillas', 'NUMERIC'),
        ('tarjetas_rojas', 'NUMERIC'),
        ('equipo', ['Sevilla', 'Real Madrid', 'Athletic', 'Elche', 'Atlético', 'Real Sociedad',
                    'Barcelona', 'Mallorca', 'Getafe', 'Osasuna', 'Cádiz', 'Celta', 'Valencia', 'Espanyol',
                    'Rayo Vallecano', 'Villarreal', 'Almería', 'Real Valladolid', 'Girona', 'Real Betis']),
        ('resultado', ['Victoria', 'Empate', 'Derrota'])
    ],
    'data': [
        (
            r['codigo_partido'],
            r['fecha'],
            r['hora'],
            r['goles'],
            r['posesion'],
            r['fueras_de_juego'],
            r['saques_de_esquina'],
            r['duelos_ganados'],
            r['duelos_perdidos'],
            r['tiros_totales'],
            r['tiros_fuera'],
            r['tiros_a_puerta'],
            r['tiros_dentro_del_area'],
            r['tiros_desde_fuera_del_area'],
            r['disparos_bloqueados'],
            r['ataques'],
            r['ataques_peligrosos'],
            r['paradas'],
            r['entradas'],
            r['pases'],
            r['pases_completados'],
            r['porcentaje_pases_completados'],
            r['faltas'],
            r['tarjetas_amarillas'],
            r['tarjetas_rojas'],
            r['equipo'],
            r['resultado']
        )
    for r in data ]
}

with open("liga_2022_23.arff", 'w', encoding='utf-8') as arff_file:
    arff.dump(arff_dict, arff_file)

## 4. Conclusión

Tras esperar unos cuantos minutos, tenemos la base de datos de todos los partidos de la temporada 2022-2023 de la liga, algo que manualmente nos hubiera llevado bastante más tiempo, y sobre todo, mucha paciencia. A partir de aquí, tocaría emplear los algoritmos y modelos vistos en la asignatura para analizar los datos y sacar conclusiones sobre el parámetro que más acerca la victoria a un equipo de fútbol, el rendimiento necesario para obtener buenos resultados o simplemente tener un modelo que predice los resultados de los partidos dadas las estadísticas de un equipo para hacer apuestas con los amigos (se tendrían que fiar de que no has visto el partido o el resultado en alguna parte, y por supuesto, callarse las estadísticas del otro equipo, en especial el número de goles). Aunque eso ya es otro trabajo.